## Análisis de la etapa de generación de medios

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np  

## Armado del dataset

En este paso parsearemos los archivos para obtener estadísticas sobre el tiempo que tarda cada ejecución de una función, sobre la memoria usada, el uso de CPU (TODO). Con esto buscamos identificar:
- Qué funciones son las que consumen mayor cantidad de memoria
- Qué funciones son las que tienen un mayor tiempo de procesamiento
- Qué funciones son las que son invocadas una mayor cantidad de veces

Una vez identificados estos puntos de análisis podemos proponer soluciones para mejorar estas estadísticas.

In [3]:
def get_function_name(function_name):
    return function_name[10:].rsplit(".c")[0]

In [4]:
relations = {
    "generate": ["gasdev"],
    "fftma2": ["covariance", "fourt", "prebuild_gwn"]
}

In [5]:
def get_data(file_name):
    data = []

    with open(file_name) as log_file:
        lines = log_file.readlines()
        for line in lines:
            row = {}
            split_line = line.split()
            if "USED" not in split_line or "ELAPSED" not in split_line: continue
            idx_used_mem = split_line.index("USED") + 4
            idx_elapsed = split_line.index("ELAPSED") + 2
            
            function_name = get_function_name(split_line[2])
            used_virtual_mem = float(split_line[idx_used_mem])
            elapsed = float(split_line[idx_elapsed].rsplit(",")[0])

            # TODO: add CPU
            row["function"] = function_name
            row["memory"] = used_virtual_mem 
            row["time"] = elapsed
            data.append(row)
            
    return data

In [18]:
def create_df(file_name):
    data = get_data(file_name)
    df = pd.DataFrame(data)
    return df.groupby(['function']).agg({'time': ['min', 'max', 'mean', 'sum', 'count'], 'memory': ['min', 'max', 'median']})

In [19]:
def analyze(file_name):
    df_grouped = create_df(file_name)
    return df_grouped.sort_values(by=('time', 'sum'), ascending=False)                

## N = 8

In [20]:
analyze('log_8.txt')

memory                  time                                \
                  min  max median       min       max      mean       sum   
function                                                                    
Py_kgeneration    2.9  2.9    2.9  0.091805  0.091805  0.091805  0.091805   
generate          2.9  2.9    2.9  0.081707  0.081707  0.081707  0.081707   
gasdev            0.0  0.5    0.0  0.000000  0.005674  0.000093  0.047828   
fftma2            0.0  0.0    0.0  0.007942  0.007942  0.007942  0.007942   
covariance        0.0  0.0    0.0  0.007492  0.007492  0.007492  0.007492   
ran2              0.0  0.5    0.0  0.000000  0.000018  0.000002  0.001708   
cov_value         0.0  0.0    0.0  0.000000  0.000030  0.000001  0.000707   
fourt             0.0  0.0    0.0  0.000079  0.000107  0.000091  0.000274   
cgrid             0.0  0.0    0.0  0.000067  0.000067  0.000067  0.000067   
length            0.0  0.0    0.0  0.000008  0.000008  0.000008  0.000024   
build_real        0.0  0.0    0.0  0.000009  0.000009  0.000009  0.000009   
prebuild_gwn      0.0  0.0    0.0  0.000007  0.000007  0.000007  0.000007   
maxfactor         0.0  0.0    0.0  0.000001  0.000001  0.000001  0.000003   
clean_real        0.0  0.0    0.0  0.000002  0.000002  0.000002  0.000002   

                      
               count  
function              
Py_kgeneration     1  
generate           1  
gasdev           512  
fftma2             1  
covariance         1  
ran2             702  
cov_value        700  
fourt              3  
cgrid              1  
length             3  
build_real         1  
prebuild_gwn       1  
maxfactor          3  
clean_real         1

## N = 16

In [20]:
analyze('log_16.txt')

memory                  time                                    \
                  min  max median       min       max          mean       sum   
function                                                                        
Py_kgeneration    4.9  4.9    4.9  0.352931  0.352931  3.529310e-01  0.352931   
generate          4.2  4.2    4.2  0.319565  0.319565  3.195650e-01  0.319565   
gasdev            0.0  0.5    0.0  0.000000  0.014654  3.830811e-05  0.156910   
fftma2            1.0  1.0    1.0  0.031217  0.031217  3.121700e-02  0.031217   
covariance        1.0  1.0    1.0  0.030104  0.030104  3.010400e-02  0.030104   
ran2              0.0  0.5    0.0  0.000000  0.000022  1.032080e-06  0.005437   
cov_value         0.0  0.5    0.0  0.000000  0.000013  8.762626e-07  0.003123   
fourt             0.0  0.0    0.0  0.000269  0.000371  3.073333e-04  0.000922   
cgrid             0.0  0.0    0.0  0.000047  0.000047  4.700000e-05  0.000047   
length            0.0  0.0    0.0  0.000008  0.000010  8.666667e-06  0.000026   
prebuild_gwn      0.0  0.0    0.0  0.000023  0.000023  2.300000e-05  0.000023   
build_real        0.0  0.0    0.0  0.000021  0.000021  2.100000e-05  0.000021   
clean_real        0.0  0.0    0.0  0.000004  0.000004  4.000000e-06  0.000004   
maxfactor         0.0  0.0    0.0  0.000000  0.000001  6.666667e-07  0.000002   

                      
               count  
function              
Py_kgeneration     1  
generate           1  
gasdev          4096  
fftma2             1  
covariance         1  
ran2            5268  
cov_value       3564  
fourt              3  
cgrid              1  
length             3  
prebuild_gwn       1  
build_real         1  
clean_real         1  
maxfactor          3

## N = 32

In [21]:
analyze('log_32.txt')

memory                  time                                    \
                  min  max median       min       max          mean       sum   
function                                                                        
Py_kgeneration    2.7  2.7    2.7  1.180846  1.180846  1.180846e+00  1.180846   
generate          4.9  4.9    4.9  0.840075  0.840075  8.400750e-01  0.840075   
gasdev           -1.3  0.5    0.0  0.000000  0.003243  1.513522e-05  0.495951   
fftma2           -2.2 -2.2   -2.2  0.338882  0.338882  3.388820e-01  0.338882   
covariance       -2.5 -2.5   -2.5  0.330282  0.330282  3.302820e-01  0.330282   
ran2             -0.3  0.5    0.0  0.000000  0.000103  9.740325e-07  0.040473   
cov_value         0.0  0.5    0.0  0.000000  0.000058  1.230344e-06  0.030296   
fourt             0.0  0.3    0.2  0.002212  0.003346  2.646333e-03  0.007939   
prebuild_gwn      0.0  0.0    0.0  0.000178  0.000178  1.780000e-04  0.000178   
build_real        0.0  0.0    0.0  0.000151  0.000151  1.510000e-04  0.000151   
clean_real        0.0  0.0    0.0  0.000104  0.000104  1.040000e-04  0.000104   
cgrid             0.0  0.0    0.0  0.000057  0.000057  5.700000e-05  0.000057   
length            0.0  0.0    0.0  0.000008  0.000016  1.300000e-05  0.000039   
maxfactor         0.0  0.0    0.0  0.000000  0.000001  4.000000e-07  0.000002   

                       
                count  
function               
Py_kgeneration      1  
generate            1  
gasdev          32768  
fftma2              1  
covariance          1  
ran2            41552  
cov_value       24624  
fourt               3  
prebuild_gwn        1  
build_real          1  
clean_real          1  
cgrid               1  
length              3  
maxfactor           5

## N = 64

In [26]:
analyze('log_64.txt')

memory                     time                        \
                  min    max median        min        max       mean   
function                                                               
Py_kgeneration  233.5  233.5  233.5  30.354270  30.354270  30.354270   
generate        168.4  168.4  168.4  21.739521  21.739521  21.739521   
gasdev           -2.9    4.4    0.0   0.000009   0.000742   0.000061   
fftma2           68.0   68.0   68.0   8.613854   8.613854   8.613854   
covariance       63.8   63.8   63.8   8.412335   8.412335   8.412335   
ran2             -0.6    0.8    0.0   0.000007   0.000281   0.000014   
cov_value        -0.7    1.0    0.0   0.000018   0.000320   0.000030   
fourt             0.3    1.7    0.4   0.051830   0.078516   0.064563   
prebuild_gwn      2.5    2.5    2.5   0.002939   0.002939   0.002939   
build_real       -0.3   -0.3   -0.3   0.002089   0.002089   0.002089   
clean_real        1.0    1.0    1.0   0.001677   0.001677   0.001677   
cgrid             0.0    0.0    0.0   0.000271   0.000271   0.000271   
length            0.0    0.0    0.0   0.000048   0.000081   0.000065   
maxfactor         0.0    0.0    0.0   0.000013   0.000015   0.000014   

                                   
                      sum   count  
function                           
Py_kgeneration  30.354270       1  
generate        21.739521       1  
gasdev          16.076987  262144  
fftma2           8.613854       1  
covariance       8.412335       1  
ran2             4.680977  333450  
cov_value        4.646094  156816  
fourt            0.193689       3  
prebuild_gwn     0.002939       1  
build_real       0.002089       1  
clean_real       0.001677       1  
cgrid            0.000271       1  
length           0.000196       3  
maxfactor        0.000056       4

## N = 128

In [29]:
analyze('log_128.txt')

5897863


memory                        time                          \
                   min     max  median         min         max        mean   
function                                                                     
Py_kgeneration  1864.7  1864.7  1864.7  126.767549  126.767549  126.767549   
generate        1759.0  1759.0  1759.0   97.731527   97.731527   97.731527   
gasdev          -134.6    18.5     0.0    0.000000    0.000772    0.000027   
fftma2           129.3   129.3   129.3   29.034783   29.034783   29.034783   
covariance        93.1    93.1    93.1   27.493769   27.493769   27.493769   
ran2              -4.8     2.2     0.0    0.000000    0.000065    0.000002   
cov_value         -0.6     0.7     0.0    0.000001    0.000281    0.000002   
fourt             -5.2    18.7     0.5    0.390409    0.591145    0.499473   
build_real         0.0     0.0     0.0    0.017085    0.017085    0.017085   
prebuild_gwn      17.0    17.0    17.0    0.014117    0.014117    0.014117   
clean_real        14.1    14.1    14.1    0.009017    0.009017    0.009017   
cgrid              0.0     0.0     0.0    0.000187    0.000187    0.000187   
length             0.0     0.0     0.0    0.000032    0.000035    0.000033   
maxfactor          0.0     0.0     0.0    0.000002    0.000003    0.000003   

                                     
                       sum    count  
function                             
Py_kgeneration  126.767549        1  
generate         97.731527        1  
gasdev           57.591066  2097152  
fftma2           29.034783        1  
covariance       27.493769        1  
ran2              4.661066  2668394  
cov_value         2.443765  1132300  
fourt             1.498418        3  
build_real        0.017085        1  
prebuild_gwn      0.014117        1  
clean_real        0.009017        1  
cgrid             0.000187        1  
length            0.000099        3  
maxfactor         0.000008        3

## N = 256

In [35]:
dfs = []
for i in range(10):
    print(i)
    df = create_df("log_256_{}.txt".format(i+1))
    dfs.append(df)

0
1
2
3
4
5
6
7
8
9


In [40]:
functions = ['Py_kgeneration', 'generate', 'fftma2', 'covariance', 'gasdev', 'fourt', 'cov_value', 'ran2', 'build_real', 'prebuild_gwn', 'clean_real', 'cgrid', 'length', 'maxfactor']


#df_final = pd.concat(dfs).sort_values(by=('time', 'sum'), ascending=False)  